## Project. Part 2: mounting file systems on Warewulf node.

The NFS exported ```/home``` is mounted on the warewulf node per the default configuration settings in ```warewulf.conf```.

### Mounting additional NFS directory.

Directory ```/opt``` is also exported from wwctX container host, but not mounted on the warewulf node by default.

To mount it, do the following:

Edit file ```/usr/local/etc/warewulf/warewulf.conf``` on the wwctX host.  

In the ```nfs:``` block,  set ```mount: true``` for the both /home abnd /opt:
```yaml
    nfs:
      enabled: true
      export paths:
      - path: /home
        export options: rw,sync
        mount options: defaults
        mount: true
      - path: /opt
        export options: ro,sync,no_root_squash
        mount options: defaults
        mount: true
      systemd name: nfs-server
```

Rebuild the overlay:
```bash
wwctl overlay build
```

Reboot the warewulf node:
```bash
ssh node08
sudo reboot
```

SSH to the node after it boots up and run command:
```bash
ssh node08
df -h
```
You should see the /opt mounted.


### Mounting a local disk as /scratch.

Enter the shell in  the warewulf container:
```bash
wwctl container shell warewulf-debian:12.0
```
Install packages ```gdisk``` and  ```ignition```:
```bash
apt install gdisk ignition
```
Exit the container:
```bash
exit
```

Add disk /dev/sda and mounting point /scratch in the node configuration. Please use your node name instead of node08 below:
```bash
wwctl node set node08 \
--diskname /dev/sda --diskwipe \
--partname scratch --partcreate --fsname scratch \
--fsformat ext4 --fspath /scratch --fswipe
```

Rebuild the overlay:
```bash
wwctl overlay build
```

Reboot the node.
```bash
ssh node08
sudo reboot
```

Check the mounted file systems after the node boots up:
```bash
ssh node08
df -h
```
You should see /dev/sda1 mounted on /scratch


### Building our own container for warewulf.

We first deployed the warewulf installation image file based on a container downloaded from github.

Now we are going to build a container on our system.

On wwctX host, install package ```podman```:
```bash
sudo apt install podman
```

Download warewulf container configurations:
```bash
cd ~/git
git clone https://github.com/warewulf/warewulf-node-images.git
```
Let's build podman container and name it debian_local:
```bash
sudo podman build -f  git/warewulf-node-images/debian/Containerfile --tag debian_local
```

Check what containers podman can see:
```bash
sudo podman images
```

Export ```localhost/debian_local``` into tar file ```debian_local.tar```:
```bash
sudo podman save localhost/debian_local -o debian_local.tar
```

Import the tar file into a warewulf container:
```bash
sudo wwctl container import file:///home/hostadm/debian_local.tar debian_local
```
Check what containers warewulf sees:
```bash
wwctl container list
```

Login to the container, install packages nano, sudo, and less:
```bash
sudo wwctl container shell debian_local
apt install nano sudo less
```

Assign the new container, ```debian_local```, to your node. For example, for node08, it runs as follows:
```bash
sudo wwctl node set node08 --container debian_local
```

Check if the node configuration has the new container listed:
```bash
wwctl node list node08 -a
```

Rebuild the overlay:
```bash
sudo wwctl overlay build
```

Reboot the node.
```bash
ssh node08
sudo reboot
```

SSH to the node, and see if it has the newer kernel running:
```bash
uname -a
```